1. Create a cosine similarity matrix for all of Shakespeare’s works found in the provided
file. This will result in a 42 by 42 matrix with the cosine similarity between each of his
works. In other words, calculate the document-wise cosine similarity between all of
Shakepeare’s works. (50 points). Use TF_IDF for this. Note, you can use the Cosine
Similarity function on scikit-learn or implement your own, but no other library/package is
allowed.


In [ ]:
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.feature_extraction.text import TfidfVectorizer
import os
import pandas as pd

In [ ]:
from zipfile import ZipFile
file_name = "/content/shakespeares-works_TXT_FolgerShakespeare.zip"

with ZipFile(file_name, 'r') as zip:
  zip.extractall("/content/shakespeares-works_TXT_FolgerShakespeare")
  print('Done')

Done


In [ ]:
data_dir = "shakespeares-works_TXT_FolgerShakespeare"
files = os.listdir(data_dir+"/")
files.remove("__MACOSX")

In [ ]:
data = []
for file in files:
    with open("/content/shakespeares-works_TXT_FolgerShakespeare/"+file, 'r') as fp:
        data.append(fp.read())

In [ ]:
tfidf_vectorizer = TfidfVectorizer()
tfidf_matrix_train = tfidf_vectorizer.fit_transform(data)  #finds the tfidf score with normalization


In [ ]:
cosine_sim = cosine_similarity(tfidf_matrix_train, tfidf_matrix_train)

In [ ]:
cosine_sim

array([[1.        , 0.59813572, 0.65459176, ..., 0.52515851, 0.57395169,
        0.69694474],
       [0.59813572, 1.        , 0.66801609, ..., 0.5890345 , 0.59258345,
        0.71771293],
       [0.65459176, 0.66801609, 1.        , ..., 0.59895863, 0.66716633,
        0.79038899],
       ...,
       [0.52515851, 0.5890345 , 0.59895863, ..., 1.        , 0.52277672,
        0.62033426],
       [0.57395169, 0.59258345, 0.66716633, ..., 0.52277672, 1.        ,
        0.70530628],
       [0.69694474, 0.71771293, 0.79038899, ..., 0.62033426, 0.70530628,
        1.        ]])

In [ ]:
df = pd.DataFrame(data = cosine_sim, columns = [file.strip(".txt") for file in files])
df.insert(loc=0, column='Row_Name', value=[file.strip(".txt") for file in files])


In [ ]:
df.to_csv("Cosine_Similarity.csv", index = False)

2. Write a function that takes the previous matrix and a number n as parameters (nothing
else will be accepted) and return the top n similar works. Use the function to output the
top 10 similar works. (30 points).


In [ ]:
def print_n_best(cosine_sim, n):
   
    sorted_sim = sorted([(i,sorted(enumerate(sim_scores), key = lambda x:x[1], reverse=True)[1]) for i, sim_scores in enumerate(cosine_sim)], key = lambda x:x[1][1], reverse = True)
    sorted_sim_temp = [str(df['Row_Name'][sim[0]])+" & "+str(df['Row_Name'][sim[1][0]]) for sim in sorted_sim]
   
    for x in sorted_sim_temp[:n]:
        print(x)

In [ ]:
print_n_best(cosine_sim,10)

venus-and-adonis_TXT_FolgerShakespeare & lucrece_TXT_FolgerShakespeare
lucrece_TXT_FolgerShakespeare & venus-and-adonis_TXT_FolgerShakespeare
henry-iv-part-1_TXT_FolgerShakespeare & henry-iv-part-2_TXT_FolgerShakespeare
henry-iv-part-2_TXT_FolgerShakespeare & henry-iv-part-1_TXT_FolgerShakespeare
shakespeares-sonnets_TXT_FolgerShakespeare & lucrece_TXT_FolgerShakespeare
henry-vi-part-1_TXT_FolgerShakespeare & henry-vi-part-2_TXT_FolgerShakespeare
henry-vi-part-2_TXT_FolgerShakespeare & henry-vi-part-1_TXT_FolgerShakespeare
richard-ii_TXT_FolgerShakespeare & richard-iii_TXT_FolgerShakespeare
richard-iii_TXT_FolgerShakespeare & richard-ii_TXT_FolgerShakespeare
henry-v_TXT_FolgerShakespeare & henry-viii_TXT_FolgerShakespeare


Bonus (20 points): Using the same methodology from questions 1 and 2, create a
similarity matrix between the 20 newsgroups corpus. And find the top 5 similar
newsgroups.

In [ ]:
from sklearn.datasets import fetch_20newsgroups
newsgroups_train = fetch_20newsgroups(subset='train')

In [ ]:
ng_dict = dict()
for data, tgt in zip(newsgroups_train.data, newsgroups_train.target_names):
    text = ng_dict.get(tgt, '')
    text += data
    ng_dict[tgt] = text

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer
tfidf_vectorizer = TfidfVectorizer()
tfidf_matrix_train = tfidf_vectorizer.fit_transform(ng_dict.values())

In [ ]:
from sklearn.metrics.pairwise import cosine_similarity
cosine_sim = cosine_similarity(tfidf_matrix_train, tfidf_matrix_train)

In [ ]:
import pandas as pd
df = pd.DataFrame(data = cosine_sim, columns = ng_dict.keys())
df.insert(loc=0, column='Row_Name', value=ng_dict.keys())

In [ ]:
print_n_best(cosine_sim, 10)

sci.crypt & talk.politics.mideast
talk.politics.mideast & sci.crypt
comp.os.ms-windows.misc & sci.crypt
talk.politics.guns & sci.crypt
sci.med & sci.crypt
alt.atheism & talk.politics.mideast
comp.sys.mac.hardware & sci.crypt
comp.windows.x & sci.crypt
soc.religion.christian & sci.crypt
rec.sport.baseball & sci.crypt


3. Using the code from the Language Models II class, train two simple language models
using all of the files (together) in shakespeares-works_TXT_FolgerShakespeare.zip. One
model should be trained using bigrams, the other using trigrams. (40 points).

In [ ]:
import nltk
nltk.download('reuters')
nltk.download('punkt')


[nltk_data] Downloading package reuters to /root/nltk_data...
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


True

In [ ]:
tokens = []
for doc in data:
 tokens.append(nltk.word_tokenize(doc))

In [ ]:
#Using Bigrams
from nltk.corpus import reuters
from nltk import bigrams, trigrams
from collections import Counter, defaultdict
# Create a placeholder for model
model_bigram = defaultdict(lambda: defaultdict(lambda: 0))
# Count frequency of co-occurence
for sentence in tokens:
  for w1, w2 in bigrams(sentence, pad_right=True, pad_left=True):
    model_bigram[w1][w2] += 1
# Let's transform the counts to probabilities
for w1 in model_bigram:
  total_count = float(sum(model_bigram[w1].values()))
  for w2 in model_bigram[w1]:
    model_bigram[w1][w2] /= total_count

In [ ]:
dict(model_bigram["King"])

{'!': 0.011428571428571429,
 "''": 0.0016326530612244899,
 "'s": 0.09551020408163265,
 ',': 0.11836734693877551,
 '--': 0.0024489795918367346,
 '.': 0.08897959183673469,
 ':': 0.004081632653061225,
 ';': 0.004081632653061225,
 '?': 0.0236734693877551,
 'And': 0.006530612244897959,
 'Be': 0.0008163265306122449,
 'Bolingbroke': 0.0008163265306122449,
 'Brothers': 0.0008163265306122449,
 'Cambyses': 0.0008163265306122449,
 'Capaneus': 0.0008163265306122449,
 'Cerberus': 0.0008163265306122449,
 'Claudius': 0.0008163265306122449,
 'Clothair': 0.0008163265306122449,
 'Cophetua': 0.0024489795918367346,
 'Digest': 0.0008163265306122449,
 'Dismiss': 0.0008163265306122449,
 'Does': 0.0008163265306122449,
 'Duncan': 0.0024489795918367346,
 'Edward': 0.027755102040816326,
 'Five': 0.0008163265306122449,
 'For': 0.0008163265306122449,
 'From': 0.0008163265306122449,
 'Gorboduc': 0.0008163265306122449,
 'Had': 0.0016326530612244899,
 'Hal': 0.0008163265306122449,
 'Hamlet': 0.0032653061224489797,
 '

In [ ]:
#Using Trigrams :
# Create a placeholder for model
#nested_dict = lambda: defaultdict(nested_dict)
model_trigram = defaultdict(lambda: defaultdict(lambda: defaultdict(lambda:0)))
# defaultdict(lambda: defaultdict(lambda: 0))
# Count frequency of co-occurence
#model_trigram.keys()
for sentence in tokens:
  #print(list(trigrams(sentence)))
  for w1, w2, w3 in trigrams(sentence, pad_right=True, pad_left=True):
   model_trigram[w1][w2][w3] += 1
# Let's transform the counts to probabilities
  for w1,dict1 in model_trigram.items():
    for w2,dict2 in dict1.items():
      total_count = float(sum(dict2.values()))
      for w3,value in dict2.items():
        model_trigram[w1][w2][w3] = value/total_count
dict(model_trigram["the"]["battle"])



{"'s": 0.25416666666666665,
 ',': 0.3167679398148148,
 '.': 0.0004352334104938272,
 'Which': 1.2056327160493825e-06,
 'and': 0.00034842785493827166,
 'came': 6.028163580246912e-07,
 'ends': 0.0020833333333333333,
 'fly': 2.8935185185185183e-05,
 "ha'": 2.8935185185185183e-05,
 'let': 0.05,
 'of': 8.680555555555555e-05,
 'range': 0.25,
 'sought': 0.025,
 'still': 0.0010416666666666667,
 'than': 7.233796296296296e-06,
 'think': 0.1,
 'thus': 2.411265432098765e-06,
 'to': 6.028163580246912e-07}

4) Write a function that takes the following three parameters: model, list of start words, number of sentences to generate. This
function should return the sentences generated as a list. DO NOT print anything to the screen from within the function. Use this
function to generate 10 sentences with the bigram model from the previous question, and 5 sentences with the trigram model from
the previous question.


In [ ]:
import random
def Gen_Sentence(model,Start_words,num_sentnc):
  sentences = []
  n_gram = len(Start_words)
  for num in range(num_sentnc):
    #print(num)
    text = Start_words
    sentence_finished = False
    while not sentence_finished:
        #print(text)
        r = random.random()
        accumulator = .0
        M = model
        for i in range(n_gram-1,0,-1):
            M=M[text[i*-1]]
        #print(M)
        for word in M.keys():
          accumulator += M[word]
          #print(r)
          if accumulator >= r:
            text.append(word)
            break

        if text[-1:] == [None]:
          sentence_finished = True
 
    sentences.append( ' '.join([t for t in text if t]))
  return sentences
 

In [ ]:
Result_bigram = Gen_Sentence(model_bigram,['the','battle'],10)

In [ ]:
Result_bigram

["the battle is good lady , to die . KING RICHARD By the dead , I know And she stoop , But Macbeth , but this good sir , Adriana , by him , '' Call hither . So your swords ? I the villain ! Ha ! How ugly monster . Enter Lovell and use with troops , it stands all men have him. -- Lord Governor . To shine , a ladder , can end . PRINCE Well met but give thee ? '' ; nor foot , Attend our host , for women are come , John the Dauphin , ho , and their Attendants . Go play the clearness . PAULINA From ashes on him . [ They kiss your eyes fly , or not possible . [ They exit . BOY , marry , think'st thou wash this noble Buckingham . FIRST SENATOR He draws . ] LE BEAU , lads , they that point . [ to the Cardinal did ransom lives , so much more marketable. -- Nay , And how to horse As if thou and virtuous visor is gone , adieu , they skip From fasting horses Pace In the ear As doth quit the horses unto the latter age , is a semicircled farthingale . Trumpets sound . If you , And bear him her . Wel

In [ ]:
Result_trigram = Gen_Sentence(model_trigram,['the','battle','to'],5)

In [ ]:
Result_trigram

["the battle to be Acquainted with this reason stands for the guests . Then two Priests Hume and Southwell , and that he shall by that virtue can not be , And from that full meridian of my conscience , Thou fall'st a blessed time ; it values not your asking . Our king has all the choicest music of the papers . ] [ The Coronation procession exits , with that blood hath the thing I have no spleen against you ? GRIFFITH Madam , you have half our power to do it -- Like goodly buildings left without a tongue which I would your Grace , Then Deputy of Ireland , and make my vouch as strong As shore of Styx ? Make haste . CASSIUS O you gods , Render me worthy of the Queen 's , The way that they have in hand here , She should have ta'en you napping , gentle hearers , know To rank our chosen truth with such furniture as suits , How you stand by awhile . [ He tries to retrieve it . [ Music , awake ! [ Enter Cardinal Wolsey , that comfort comes too late . KING Two equal men . KING , [ to Wolsey ] M